#Imports

In [47]:
import glob
import os
import shutil
import json
import csv
import networkx as nx
import matplotlib.pyplot as plt
try:
  import pyvis
  from pyvis.network import Network
except:
  !pip install pyvis
  import pyvis
  from pyvis import Network
from time import sleep

In [2]:
WORKING_DIR = "/content/drive/MyDrive/MSDS_marketing_text_analytics/master_files/3_network_analysis"

In [3]:
#!wget http://128.138.93.164/nikelululemonadidas_tweets.jsonl.gz -P /content/drive/MyDrive/MSDS_marketing_text_analytics/master_files/3_network_analysis

In [4]:
#!gzip -d /content/drive/MyDrive/MSDS_marketing_text_analytics/master_files/3_network_analysis/nikelululemonadidas_tweets.jsonl.gz

#Data Prep

In [52]:
json_file = open('%s/nikelululemonadidas_tweets.jsonl' % WORKING_DIR, 'r')

There's a lot of metadata in a tweet! If you want to take a look at all that you can get from a tweet:
https://developer.twitter.com/en/docs/twitter-api/v1/data-dictionary/object-model/tweet

In [53]:
uniqueusers = {}

for i, atweet in enumerate(json_file):
    if i < 50:
      tweetjson = json.loads(atweet)
      text = tweetjson['full_text']
      if "nike" in text:
        print(text)

Via Nike⁠ SNKRS: can I get a W ⁦@Nike⁩ ⁦@nikebasketball⁩ #snkrs  https://t.co/lQ6zKN1Oq6
@Kaya_Alexander5 @nikestore @Nike @SneakerAdmirals Jelly!   Awesome pair https://t.co/L2Kefg2fUP
RT @WALionsFB: Game Recap from #MondayNightFootball‼️🏈 @jumpman23 @usnikefootball @wacad @larryblustein @RiddellSports @Nike @FlaHSFootball…
@somaliboxer @AlisSistersClub @nikelondon @Nike Fists up ❤️
RT @NiaOnAir: Identity is not as simple as black and white. ☯ On episode 5 of @nike's #ComeThru, I get into it with @lisa_asano, @whoisumi,…
RT @WALionsFB: Game Recap from #MondayNightFootball‼️🏈 @jumpman23 @usnikefootball @wacad @larryblustein @RiddellSports @Nike @FlaHSFootball…
Liquid3_6 Sneaker Of The Day @nike 

Saquon Barkley x Nike Air Trainer 3
Color: Pearl White/Neptune Green-Sail
Style Code: DA5403-200
Release Date: October 8, 2021
Price: $140
#sneakerhead #style #fashion #sneakeroftheday #sneakers #footwear #brandmarketing #Nike #Liquid3_6🛸 https://t.co/kwIROtsn1k


In [ ]:
json_file = open('%s/nikelululemonadidas_tweets.jsonl' % WORKING_DIR, 'r')

In [6]:
# Identify unique users in the mention network
uniqueusers = {}

for i, atweet in enumerate(json_file):
    if i % 10000 == 0:
      print("%s tweets iterated" % i)
    tweetjson = json.loads(atweet)
    userwhotweeted = tweetjson['user']['screen_name']
    idwhotweeted = tweetjson['user']['id']
    followercount = tweetjson['user']['followers_count']
    if idwhotweeted in uniqueusers:
      uniqueusers[idwhotweeted]['tweet_count'] += 1
    if idwhotweeted not in uniqueusers:
      uniqueusers[idwhotweeted] = {}
      uniqueusers[idwhotweeted]['tweet_count'] = 1
      uniqueusers[idwhotweeted]['id'] = idwhotweeted
      uniqueusers[idwhotweeted]['followers_count'] = followercount


0 tweets iterated
10000 tweets iterated
20000 tweets iterated
30000 tweets iterated
40000 tweets iterated
50000 tweets iterated
60000 tweets iterated
70000 tweets iterated
80000 tweets iterated
90000 tweets iterated
100000 tweets iterated
110000 tweets iterated
120000 tweets iterated
130000 tweets iterated
140000 tweets iterated
150000 tweets iterated
160000 tweets iterated
170000 tweets iterated


In [7]:
i

175077

We have 175k tweets! That's a lot of shoe talk.

In [8]:
len(uniqueusers)

104772

And we have 104k users

In [9]:
userstoinclude = set()

# a set is a unique list
usercount = 0
for auser in uniqueusers:
  if uniqueusers[auser]['tweet_count'] > 1: # if any user has more than 2 tweets 
    if uniqueusers[auser]['followers_count'] > 100000: # if any user has more than 2500 followers
      usercount += 1
      userstoinclude.add(auser)
print(len(userstoinclude))

196


So let's take a minute to define the audience we just cut out of the Twitter data. This is a "marketing" specialization, anyways. We made two big changes to our population to get the number of nodes (users we're going to include) down to something reasonable. ***We first filtered out folks who didn't tweet at least three times about any of these brands. We also put in a requirement that the account had to have greater than 100k followers***

So in marketing terms who are these people? Well 2+ tweets in a 3-month span, about these brands specifically. These have to be people two regularly talk about athletic wear. Did you or I tweet 3x in the last three months about these brands. Probably not. These are folks who are engaged with these brands.

Second, we put a pretty hefty follower count restriction in. The average Twitter follower has under a hundred followers (think: far, far under). So 100,000 people, these have to be either brand accounts, or individuals that are very influential online, offline or both. 

So we have engaged influentials. If we're presenting this data to someone, that can't be lost. These aren't just common folks tweetin' about Nike.

In [10]:
len(userstoinclude) / len(uniqueusers) 

0.0018707288206772801

A 99% reduction in our nodes. That's a pretty steep cut, and I worry that if we go any higher we're just going to get bots or brands who regularly tweet about one or all of these brands. P.S. -- let's face it, there are bots in this. What would I do to try and mitigate this? I'd run the `userstoinclude` through Botometer:
https://botometer.osome.iu.edu/api

If you want an advanced course where we do things like this, let me know!

In [11]:
json_file = open('%s/nikelululemonadidas_tweets.jsonl' % WORKING_DIR, 'r')

There's a lot of metadata in a tweet! If you want to take a look at all that you can get from a tweet:
https://developer.twitter.com/en/docs/twitter-api/v1/data-dictionary/object-model/tweet

Now let's load the edges into a Networkx graph. Note we're recording the mentions (who mentions who in a tweet). We're implying a direction, and thus making a directed network.

In [12]:
Graph = nx.DiGraph()

In [13]:
# Identify unique users in the mention network
all_tweets = {}

for i, atweet in enumerate(json_file):
    if i % 10000 == 0:
      print("%s tweets iterated" % i)
    tweetjson = json.loads(atweet)
    userwhotweeted = tweetjson['user']['screen_name']
    idwhotweeted = tweetjson['user']['id']
    followercount = tweetjson['user']['followers_count']
    if idwhotweeted in userstoinclude:
      users = tweetjson['entities']['user_mentions']
      if len(users) > 0:
          for auser in users:
              screenname = auser['screen_name']
              mentionid = auser['id']
              if mentionid in userstoinclude:
                Graph.add_edge(userwhotweeted, screenname)

0 tweets iterated
10000 tweets iterated
20000 tweets iterated
30000 tweets iterated
40000 tweets iterated
50000 tweets iterated
60000 tweets iterated
70000 tweets iterated
80000 tweets iterated
90000 tweets iterated
100000 tweets iterated
110000 tweets iterated
120000 tweets iterated
130000 tweets iterated
140000 tweets iterated
150000 tweets iterated
160000 tweets iterated
170000 tweets iterated


In [14]:
nx.info(Graph)

'DiGraph with 126 nodes and 210 edges'

In [55]:
fig, ax = plt.subplots(1, 1, figsize=(300, 300))
#ugh these settings are such a pain, but here's the way to look them up: 
#https://networkx.org/documentation/stable/reference/generated/networkx.drawing.nx_pylab.draw_networkx.html
nx.draw_networkx(Graph, ax=ax, font_color="#FFFFFF", font_size=20, node_size=30000, width=4, arrowsize=100)
plt.savefig("%s/mention_network.png" % WORKING_DIR, format="PNG")

In [54]:
nt = Network('1000', '600', directed=True, notebook=True, layout='force_atlas_2based')
# populates the nodes and edges data structures
nt.from_nx(Graph)
nt.show_buttons(filter_=['physics'])
#nt.show('nx.html')
from IPython.core.display import display, HTML
display(HTML('nx.html'))